In [275]:
import pandas as pd
import numpy as np
import json
import geopandas as gpd
import plotly.express as px

In [276]:
collisions_data = pd.read_csv('data/working/traffic_wards_cleaned.csv')
with open('data/demography/Wards_2022-2026.geojson', 'r') as f:
    wards = json.load(f)
## wards = wards['features']

In [277]:
# Cleaning and organizing data for the chart
count_collisions = pd.pivot_table(collisions_data, index=['ward_name', 'ward_number'], aggfunc='count')
count_collisions = count_collisions['ID']
count_collisions = count_collisions.drop('Unknown', axis='index')
count_collisions = count_collisions.reset_index()
count_collisions

ward_name ward_number    ID
0                      Alta Vista          18  4083
1                  Barrhaven East          24  1703
2                  Barrhaven West           3  2076
3                             Bay           7  3664
4            Beacon Hill-Cyrville          11  3305
5                         Capital          17  4393
6                         College           8  5211
7            Gloucester-Southgate          10  4159
8                    Kanata North           4  1883
9                    Kanata South          23  2127
10                   Kitchissippi          15  4051
11              Knoxdale-Merivale           9  4367
12        Orléans East-Cumberland           1  2258
13            Orléans South-Navan          19  1773
14             Orléans West-Innes           2  2701
15                        Osgoode          20  2508
16                    Rideau-Jock          21  2425
17              Rideau-Rockcliffe          13  2683
18                  Rideau-Vanier          12  5201
19                          River          16  3886
20  Riverside South-Findlay Creek          22  1071
21                       Somerset          14  5177
22                    Stittsville           6  1404
23            West Carleton-March           5  2329

In [278]:
# Add the id of the ward name to the geojson file
for k in range(len(wards['features'])):
    wards['features'][k]['id'] = wards['features'][k]['properties']['WARD']
wards['features'][0]['id']

'14'

In [279]:
count_collisions

ward_name ward_number    ID
0                      Alta Vista          18  4083
1                  Barrhaven East          24  1703
2                  Barrhaven West           3  2076
3                             Bay           7  3664
4            Beacon Hill-Cyrville          11  3305
5                         Capital          17  4393
6                         College           8  5211
7            Gloucester-Southgate          10  4159
8                    Kanata North           4  1883
9                    Kanata South          23  2127
10                   Kitchissippi          15  4051
11              Knoxdale-Merivale           9  4367
12        Orléans East-Cumberland           1  2258
13            Orléans South-Navan          19  1773
14             Orléans West-Innes           2  2701
15                        Osgoode          20  2508
16                    Rideau-Jock          21  2425
17              Rideau-Rockcliffe          13  2683
18                  Rideau-Vanier          12  5201
19                          River          16  3886
20  Riverside South-Findlay Creek          22  1071
21                       Somerset          14  5177
22                    Stittsville           6  1404
23            West Carleton-March           5  2329

In [280]:

fig = px.choropleth(
    count_collisions,
    geojson=wards,
    locations="ward_name",
    featureidkey="id",
    color="ID",
    color_continuous_scale="Viridis",
    range_color=(0, 12),
    # scope="europe",
    labels={"ID": "Count Accidents"},
)
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
fig.update_geos(fitbounds="locations", visible=True)
fig.show()

In [281]:
import requests
polygons = requests.get(
    "https://raw.githubusercontent.com/isellsoap/deutschlandGeoJSON/main/4_kreise/2_hoch.geo.json"
).json()

In [282]:
polygons

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 0,
   'properties': {'ID_0': 86,
    'ISO': 'DEU',
    'NAME_0': 'Germany',
    'ID_1': 9,
    'NAME_1': 'Niedersachsen',
    'ID_2': 23,
    'NAME_2': 'Weser-Ems',
    'ID_3': 244,
    'NAME_3': 'Oldenburg',
    'NL_NAME_3': None,
    'VARNAME_3': None,
    'TYPE_3': 'Landkreise',
    'ENGTYPE_3': 'Rural district'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[8.65347957611084, 53.11003112792969],
      [8.66598987579357, 53.106590270996094],
      [8.672159194946346, 53.10675048828125],
      [8.666389465332088, 53.099151611328125],
      [8.666588783264217, 53.09542846679699],
      [8.673138618469295, 53.088119506835994],
      [8.691630363464412, 53.08853149414068],
      [8.69798946380621, 53.084960937500114],
      [8.70414924621582, 53.08509063720709],
      [8.710700035095215, 53.077781677246094],
      [8.711669921874943, 53.05915069580084],
      [8.705711364746207, 53.05529022216797],
     

In [283]:
wards['features'][0]['properties']

{'NAME': 'Somerset',
 'NAME_FR': 'Somerset',
 'WARD': '14',
 'SECTOR_EN': 'Urban',
 'SECTOR_FR': 'Urbain',
 'OBJECTID': 25,
 'GLOBALID': '{03C7C83F-DB65-49CC-BB4A-492ACC592896}',
 'CREATED_DATE': '2021-10-14T10:42:04Z',
 'LAST_EDITED_DATE': '2021-10-14T10:42:04Z',
 'SHAPE_Length': 16122.636670115575,
 'SHAPE_Area': 13126980.126472551}

In [284]:
gdf = gpd.GeoDataFrame.from_features(wards)

In [285]:
gdf['count_collisions'] = count_collisions['ID']


In [286]:
px.choropleth_mapbox(gdf,
                           geojson=gdf.geometry,
                           locations=gdf.WARD,
                           color=gdf.count_collisions,
                           color_continuous_scale="Viridis",
                           opacity = 0.5,
                           hover_data=["NAME"],
                           center = {'lat': 45.4201, 'lon': -75.695000},
                           labels = {'NAME' : 'NAME'},
                           mapbox_style='carto-positron')

In [287]:
gdf

geometry  \
0   POLYGON ((-75.68649 45.42139, -75.68904 45.422...   
1   POLYGON ((-75.87327 45.29769, -75.87485 45.300...   
2   POLYGON ((-75.93843 45.37184, -75.93857 45.371...   
3   POLYGON ((-75.67376 45.41652, -75.67402 45.416...   
4   POLYGON ((-75.70921 45.39693, -75.70931 45.397...   
5   POLYGON ((-75.61727 45.45038, -75.61870 45.453...   
6   POLYGON ((-75.33419 45.52486, -75.33832 45.532...   
7   POLYGON ((-75.61663 45.41182, -75.61835 45.412...   
8   POLYGON ((-75.70785 45.39504, -75.70785 45.395...   
9   POLYGON ((-75.82714 45.34225, -75.82417 45.342...   
10  POLYGON ((-75.70405 45.35180, -75.70410 45.352...   
11  POLYGON ((-75.88463 45.28418, -75.88659 45.285...   
12  POLYGON ((-75.32537 45.50937, -75.33319 45.507...   
13  POLYGON ((-75.59211 45.42084, -75.59231 45.420...   
14  POLYGON ((-75.58532 45.33392, -75.58470 45.334...   
15  POLYGON ((-75.87805 45.30635, -75.87678 45.304...   
16  POLYGON ((-76.09067 45.51910, -76.09751 45.520...   
17  POLYGON ((-75.52653 45.49557, -75.52665 45.495...   
18  POLYGON ((-75.57666 45.33794, -75.57824 45.340...   
19  POLYGON ((-75.80474 45.28108, -75.80500 45.281...   
20  POLYGON ((-75.66291 45.41698, -75.66291 45.416...   
21  POLYGON ((-75.48382 45.41985, -75.49120 45.420...   
22  POLYGON ((-75.69765 45.30377, -75.69689 45.304...   
23  POLYGON ((-75.78833 45.29284, -75.79025 45.296...   

                             NAME                      NAME_FR WARD SECTOR_EN  \
0                        Somerset                     Somerset   14     Urban   
1                    Kanata South                   Kanata-Sud   23  Suburban   
2                    Kanata North                  Kanata-Nord    4  Suburban   
3                         Capital                     Capitale   17     Urban   
4                    Kitchissippi                 Kitchissippi   15     Urban   
5               Rideau-Rockcliffe            Rideau-Rockcliffe   13     Urban   
6         Orléans East-Cumberland       Orléans-Est-Cumberland    1  Suburban   
7                      Alta Vista                   Alta Vista   18     Urban   
8                           River                      Rivière   16     Urban   
9                             Bay                         Baie    7     Urban   
10              Knoxdale-Merivale            Knoxdale-Merivale    9     Urban   
11                    Stittsville                  Stittsville    6  Suburban   
12            Orléans South-Navan            Orléans-Sud-Navan   19  Suburban   
13           Beacon Hill-Cyrville         Beacon Hill-Cyrville   11     Urban   
14           Gloucester-Southgate         Gloucester-Southgate   10     Urban   
15                        College                      Collège    8     Urban   
16            West Carleton-March          West Carleton-March    5     Rural   
17             Orléans West-Innes          Orléans-Ouest-Innes    2  Suburban   
18  Riverside South-Findlay Creek  Riverside-Sud-Findlay Creek   22  Suburban   
19                    Rideau-Jock                  Rideau-Jock   21     Rural   
20                  Rideau-Vanier                Rideau-Vanier   12     Urban   
21                        Osgoode                      Osgoode   20     Rural   
22                 Barrhaven East                Barrhaven-Est   24  Suburban   
23                 Barrhaven West              Barrhaven-Ouest    3  Suburban   

    SECTOR_FR  OBJECTID                                GLOBALID  \
0      Urbain        25  {03C7C83F-DB65-49CC-BB4A-492ACC592896}   
1   Suburbain        26  {086F1700-E394-4394-8EC8-1760EA820512}   
2   Suburbain        27  {20002E33-7AE6-4D89-B234-E7AC1884B814}   
3      Urbain        28  {3E049BC7-E873-4B10-8577-465AAD95805A}   
4      Urbain        29  {3FFF07C4-3187-42F7-A410-27C87A9041B4}   
5      Urbain        30  {4E4EC93D-29C2-4C65-8B86-83473F4F6DF9}   
6   Suburbain        31  {547D62B7-A18A-4330-B415-CDE96D706B66}   
7      Urbain        32  {611A45BF-A862-47F4-8B51-C49F4B1